In [27]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.ticker import LinearLocator
import math
from scipy import signal
import soundfile as sf
import IPython.display as ipd

## Source Generation

In [28]:
noteMap = {
    'Ab': -11,
    'A': 12,
    'A#': 13,
    'Bb': 13,
    'B': 14,
    'C': 3,
    'C#': 4,
    'Db': 4,
    'D': 5,
    'D#': 6,
    'Eb': 6,
    'E': 7,
    'F': 8,
    'F#': 9,
    'Gb': 9,
    'G': 10,
    'G#': 11,
}
# Pass in tuple, for example ('A', 4)
def noteToHz(note):
    halfNotes = noteMap.get(note[0], None)
    if halfNotes is None:
        raise RuntimeError("Invalid note entered")
    midiNote = 21 + halfNotes + (12 * note[1])
    return math.pow(2, float(midiNote-69) / 12.0) * 440.0

In [29]:
sr = 48000

In [30]:
class ADSR(object):
    # Attack, Decay, Release
    def __init__(self, atk, dec, sus, rel):
        self.atk = int(atk * sr)
        self.dec = int(dec * sr)
        self.sus = sus
        self.rel = int(rel * sr)
        self.pos = 0
        self.lastVal = 0
        self.isNoteOn = True
        
    def noteOff(self):
        if self.isNoteOn:
            self.isNoteOn = False
            self.pos = 0
            
    def hasEnded(self):
        return not self.isNoteOn and self.pos > self.rel

    def render(self, buffer):
        for i in range(len(buffer)):
            val = 0
            if self.isNoteOn:
                if self.pos < self.atk:
                    val = float(self.pos) / float(self.atk)
                elif self.pos < (self.atk + self.dec):
                    a = float(self.pos - self.atk) / self.dec
                    val = (1-a) + self.sus * a
                else:
                    val = self.sus
                self.lastVal = val
            else:
                if self.pos < self.rel:
                    a = float(self.pos) / float(self.rel)
                    val = (1-a) * self.lastVal
            buffer[i] = buffer[i] * val
            self.pos += 1
                
class SineWaveNaive(object):
    def __init__(self, freq):
        self.freq = freq
        self.phi = 0
        
    def render(self, buffer):
        for i in range(len(buffer)):
            buffer[i] = math.sin(self.phi * 2 * math.pi)
            self.phi += float(self.freq) / float(sr)
            while self.phi > 1.0:
                self.phi -= 1.0
                
class SquareWaveAdditive(object):
    def __init__(self, freq, numHarmonics=10, amp=1):
        self.freq = freq
        self.numHarmonics = numHarmonics
        self.phis = np.zeros(self.numHarmonics)
        self.amp = amp * 4 / math.pi
        self.phiDeltas = np.zeros(self.numHarmonics)
        
        for i in range(self.numHarmonics):
            harmonicFreq = float(self.freq) * (float(i) * 2 + 1)
            self.phiDeltas[i] = harmonicFreq / float(sr)
        
    def render(self, buffer):
        for i in range(len(buffer)):
            for j in range(self.numHarmonics):
                buffer[i] += math.sin(2 * math.pi * self.phis[j]) * self.amp / (float(j) * 2 + 1)
                self.phis[j] += self.phiDeltas[j]
                while self.phis[j] >= 1:
                    self.phis[j] -= 1
    
class SineWave(object):
    def __init__(self, freq):
        self.freq = freq
        self.phi = 0
        self.table_size = 24000
        
        empty_table = np.zeros(self.table_size) #a single sine wave cycle in 24000 samples
        for i in range(self.table_size):
            empty_table[i] += math.sin(2 * math.pi * i/self.table_size)
        self.table = empty_table
    
    def render(self, buffer):
        rate = self.freq * self.table_size / sr #reading rate of the table calculated with the sample rate
        for i in range(len(buffer)):
            idx_float = (rate*self.phi)%self.table_size #float location
            idx_int = int(idx_float) #floor int location
            
            #avoid bound error
            zero = idx_int-1
            two = idx_int+1
            three = idx_int+2
            if zero < 0: 
                zero = 0 
            if three > self.table_size-1: 
                two = self.table_size-1
                three = self.table_size-1
            if three > self.table_size-2:
                three = self.table_size-1

            y0 = self.table[zero]
            y1 = self.table[idx_int]
            y2 = self.table[two]
            y3 = self.table[three]
            mu = idx_float - idx_int
            #Cubic Interpretation
            mu2 = mu*mu;
            a0 = y3 - y2 - y0 + y1;
            a1 = y0 - y1 - a0;
            a2 = y2 - y0;
            a3 = y1;

            value = a0*mu*mu2+a1*mu2+a2*mu+a3
            buffer[i] = value
            
            self.phi += 1 #phi keeps adding up as long as the audio is rendering. Should it be reset at all?

class SawWave(object):
    def __init__(self, freq):
        self.freq = freq
        self.phi = 0
        self.table_size = 24000
        
        empty_table = np.zeros(self.table_size) #a single sine wave cycle in 24000 samples
        for n in range(20): #20 harmonics
            n += 1
            for i in range(self.table_size):
                empty_table[i] += (1/n) * math.sin(2 * n * math.pi * i/self.table_size)
        self.table = empty_table
    
    def render(self, buffer):
        rate = self.freq * self.table_size / sr #reading rate of the table calculated with the sample rate
        for i in range(len(buffer)):
            idx_float = (rate*self.phi)%self.table_size #float location
            idx_int = int(idx_float) #floor int location
            
            #avoid bound error
            zero = idx_int-1
            two = idx_int+1
            three = idx_int+2
            if zero < 0: 
                zero = 0 
            if three > self.table_size-1: 
                two = self.table_size-1
                three = self.table_size-1
            if three > self.table_size-2:
                three = self.table_size-1

            y0 = self.table[zero]
            y1 = self.table[idx_int]
            y2 = self.table[two]
            y3 = self.table[three]
            mu = idx_float - idx_int
            #Cubic Interpretation
            mu2 = mu*mu;
            a0 = y3 - y2 - y0 + y1;
            a1 = y0 - y1 - a0;
            a2 = y2 - y0;
            a3 = y1;

            value = a0*mu*mu2+a1*mu2+a2*mu+a3
            buffer[i] = value
            
            self.phi += 1 #phi keeps adding up as long as the audio is rendering. Should it be reset at all?

In [31]:
class PlayingNote(object):
    def __init__(self, note, noteLength, amp):
        self.effects = []
        self.amp = amp
        self.lifetimeSamples = noteLength * sr
        self.envelope = ADSR(0.1, 0.2, 0.4, 0.1)
#         self.source = SineWave(noteToHz(note))
        self.source = SawWave(noteToHz(note))
        
    def hasEnded(self):
        return self.envelope.hasEnded()
        
    def render(self, buffer):
        outBuffer = np.zeros(len(buffer))
        self.source.render(outBuffer)
        outBuffer *= self.amp
        self.envelope.render(outBuffer)

        if self.lifetimeSamples > 0:
            self.lifetimeSamples -= len(buffer)
            if self.lifetimeSamples <= 0:
                self.envelope.noteOff()

        for effect in self.effects:
            effect.render(outBuffer)

        buffer += outBuffer

class Instrument(object):
    def __init__(self):
        self.playingNotes = []
        self.instrumentEffects = []
        
    def makePlayingNote(self, note):
        return PlayingNote(note, 2, 0.25)
    
    def playNote(self, note):
        self.playingNotes.append(self.makePlayingNote(note))
    
    def render(self, buffer):
        for playingNote in self.playingNotes:
            playingNote.render(buffer)
        for effect in self.instrumentEffects:
            effect.render(buffer)
            
        # Cleanup finished notes
        self.playingNotes = list(filter(lambda playingNote: not playingNote.hasEnded(),
                                  self.playingNotes))

class Orchestra(object):
    def __init__(self):
        self.instruments = [
            Instrument()
        ]
        self.globalEffects = []
#         self.globalEffects = [Delay()]
#         self.globalEffects = [SimpleChorus()]
#         self.globalEffects = [FlangerFB()]
#         self.globalEffects = [Tremolo()]

    def render(self, buffer):
        for instrument in self.instruments:
            instrument.render(buffer)
        for effect in self.globalEffects:
            effect.render(buffer)

In [32]:
class Score(object):
    def __init__(self):
        self.orchestra = Orchestra()
        self.notes = [('A', 3), ('C', 4), ('E', 4), ('C', 4)]
        self.noteIdx = 0
        self.beatLengthInSamples = int(0.75 * sr)
        self.curBeatPos = 0
    
    def render(self, buffer):
        while self.curBeatPos <= 0:
            self.orchestra.instruments[0].playNote(
                self.notes[self.noteIdx]
            )
            self.noteIdx = (self.noteIdx + 1) % len(self.notes)
            self.curBeatPos += self.beatLengthInSamples
        self.orchestra.render(buffer)
        self.curBeatPos -= len(buffer)

## Biquad Filters
http://shepazu.github.io/Audio-EQ-Cookbook/audio-eq-cookbook.html

In [33]:
class BiquadFilter(object):
    def __init__(self, filterType):
        self.filterType = filterType  # 'HP' or 'LP'
        self.f0 = 3000  # center frequency
        self.q = 1      # Q factor
        self.xn1 = 0    # x[n-1]  
        self.xn2 = 0    # x[n-2]  
        self.yn1 = 0    # y[n-1]  
        self.yn2 = 0    # y[n-2]  
    
    def calCoeff(self, filterType, f0, q):
        w0 = 2 * math.pi * f0 / sr
        alpha = math.sin(w0) / (2 * q)
        
        if filterType == 'LP':
            b0 = (1 - math.cos(w0)) / 2
            b1 = 1 - math.cos(w0)
            b2 = (1 - math.cos(w0)) / 2
            a0 = 1 + alpha
            a1 = -2 * math.cos(w0)
            a2 = 1 - alpha
            
        elif filterType == 'HP':
            b0 = (1 + math.cos(w0)) / 2
            b1 = - (1 + math.cos(w0))
            b2 = (1 + math.cos(w0)) / 2
            a0 = 1 + alpha
            a1 = -2 * math.cos(w0)
            a2 = 1 - alpha
            
        else:
            raise RuntimeError("Undefined filter type")
            
        return b0, b1, b2, a0, a1, a2
    
    def render(self, buffer):
        b0, b1, b2, a0, a1, a2 = self.calCoeff(self.filterType, self.f0, self.q)
        x = buffer
        
        for i in range(len(buffer)):
            s = x[i]
            buffer[i] = self.yn2
            y = (b0 / a0) * s + (b1 / a0) * self.xn1 + (b2 / a0) * self.xn2 \
                              - (a1 / a0) * self.yn1 - (a2 / a0) * self.yn2
            self.xn2 = self.xn1
            self.xn1 = s
            self.yn2 = self.yn1
            self.yn1 = y

## Ring Buffer

In [34]:
class RingBuffer(object):
    def __init__(self, maxDelay):
        self.maxDelay = maxDelay + 1
        self.buf = np.zeros(self.maxDelay)
        self.writeInd = 0

    def pushSample(self, s):
        self.buf[self.writeInd] = s
        self.writeInd = (self.writeInd + 1) % self.maxDelay

    def delayedSample(self, d):
        d = min(self.maxDelay - 1, max(0, d))
        i = ((self.writeInd + self.maxDelay) - d) % self.maxDelay
        return self.buf[i]

# Linear Interpolation
class LinearWrap(object):
    def __init__(self, it):
        self.it = it
        
    def __len__(self):
        return len(self.it)
        
    def __setitem__(self, inI, val):
        if type(inI) != int:
            raise RuntimeError('Can only write to integer values')
        self.it[inI] = val

    def __getitem__(self, inI):
        loI = math.floor(inI)
        hiI = math.ceil(inI)
        a = inI - loI
        inRange = lambda val: val >= 0 and val < len(self.it)
        loX = self.it[loI] if inRange(loI) else 0
        hiX = self.it[hiI] if inRange(hiI) else 0
        return loX * (1-a) + hiX * a

# Wrap inner iterable inside RingBuffer with float indexable array
class LinearRingBuffer(RingBuffer):
    def __init__(self, maxDelay):
        self.maxDelay = maxDelay + 1
        self.buf = LinearWrap(np.zeros(self.maxDelay))
        self.writeInd = 0

In [35]:
class Delay(object):
    def __init__(self):
        self.delayTime = 0.25
        self.delaySamps = int(self.delayTime * sr)
        self.ringBuf = RingBuffer(self.delaySamps)
        
    def render(self, buffer):
        for i in range(len(buffer)):
            s = buffer[i]
            self.ringBuf.pushSample(s)
            buffer[i] = s * 0.5 + self.ringBuf.delayedSample(self.delaySamps) * 0.5

## Modulated Effects

In [36]:
class Tremolo(object):
    def __init__(self):
        self.fmod = 5
        self.alpha = 0.5
        self.BL = 0.5
        self.phi = 0
        
    def render(self, buffer):
        x = LinearWrap(buffer)
        deltaPhi = self.fmod/sr

        for i in range(len(buffer)):
            s = x[i]
            trem = 1 + self.alpha * math.sin(2 * math.pi * self.phi)
            buffer[i] = s * self.BL + s * trem

            self.phi = self.phi + deltaPhi
            while self.phi >= 1:
                self.phi -= 1

In [37]:
class SimpleChorus(object):
    def __init__(self):
        self.fmod = 1.5
        self.A = int(0.002 * sr)
        self.M = int(0.002 * sr)
        self.BL = 1.0
        self.FF = 0.7
        self.maxDelaySamps = self.M + self.A + 2
        self.ringBuf = LinearRingBuffer(self.maxDelaySamps)
        self.phi = 0
        
    def render(self, buffer):
        x = LinearWrap(buffer)
        deltaPhi = self.fmod/sr

        for i in range(len(buffer)):
            s = x[i]
            self.ringBuf.pushSample(s)
            delaySamps = int(math.sin(2 * math.pi * self.phi) * self.maxDelaySamps)
            buffer[i] = s * self.BL + self.ringBuf.delayedSample(delaySamps) * self.FF

            self.phi = self.phi + deltaPhi
            while self.phi >= 1:
                self.phi -= 1

In [38]:
class FlangerFB(object):
    def __init__(self):
        self.fmod = 0.1
        self.A = int(0.005 * sr)
        self.M = int(0.005 * sr)
        self.BL = 0.7
        self.FF = 0.7
        self.FB = -0.7
        self.maxDelaySamps = self.M + self.A + 2
        self.ringBuf = LinearRingBuffer(self.maxDelaySamps)
        self.prevDelaySamp = 0
        self.phi = 0
    
    def render(self, buffer):
        x = LinearWrap(buffer)
        deltaPhi = self.fmod/sr
        
        for i in range(len(buffer)):
            s = x[i] + self.prevDelaySamp * self.FB
            self.ringBuf.pushSample(s)
            delaySamps = self.M + int(math.sin(2 * math.pi * self.phi) * self.A)
            self.prevDelaySamp = self.ringBuf.delayedSample(delaySamps)
            buffer[i] = s * self.BL + self.prevDelaySamp * self.FF

            self.phi = self.phi + deltaPhi
            while self.phi >= 1:
                self.phi -= 1

## Audio Output

### Synth output

In [39]:
def playScore(filename, length, score):
    bufSize = 4096
    buffer = np.zeros(bufSize)
    lengthSamples = int(length * sr)
    numBlocks = int(lengthSamples / bufSize) + 1
    
    with sf.SoundFile(filename, 'wb', sr, 1) as f:
        for i in range(numBlocks):
            buffer *= 0
            score.render(buffer)
            f.write(buffer)

file_output = 'audio/output/testScore.wav'
playScore(file_output, 10, Score())
ipd.Audio(file_output, rate=sr)

### Test using audio

In [40]:
def playAudio(inFile, outFile, effect):
    x, sr = sf.read(inFile)
    bufSize = 4096
    lengthSamples = len(x)
    numBlocks = int(lengthSamples / bufSize) + 1
    
    with sf.SoundFile(outFile, 'wb', sr, 1) as f:
        for i in range(numBlocks):
            buffer = x[bufSize * i: bufSize * (i+1)]
            effect.render(buffer)
            f.write(buffer)

In [25]:
# original audio
inFile = 'audio/input/sv.wav'
ipd.Audio(inFile, rate=sr)